# Data Science Project: Finding the Best Locations for New Supermarkets in Munich
Welcome to the data collection and preprocessing notebook for the project **"Finding the Best Locations for New Supermarkets in Munich"**. This notebook demonstrates how to collect, clean, and prepare both supermarket location data and population data for spatial analysis and modeling. The workflow includes:
- Automated supermarket location data collection in the Munich area using the Google Places API.
- Integration of publicly available population data on a 100m grid.
- Data cleaning, standardization, and visualization to support downstream modeling.
This notebook is part of a larger project aimed at identifying high-opportunity areas for new supermarket openings using advanced spatial data science techniques.

In [ ]:
import numpy as np
import plotly.express as px
import pandas as pd
import requests
import time

import re
from pyproj import Transformer

from sklearn.neighbors import BallTree
import numpy as np

## All grocery stores in Munich

Scan on a grid of step size ~2 km in the Munich area because GooglePlaces returns max. 60 results per query.

In [ ]:
# Check: 0.016 deg Lat is 1.8km
np.radians(0.016)*6371 # earth radius

1.7791188263129398

In [ ]:
# Check if the lat lon range is large enough for the scan
CITY_CENTER = (48.1351, 11.5820)  # Munich center
lat_step = 0.016  # ~1.8 km
lon_step = 0.024  # ~1.8 km for Munich

# Create a grid of coordinates around the city center
lat_range = [CITY_CENTER[0] + i * lat_step for i in range(-10, 11)] # Effective total scan for 1st and 2nd run
lon_range = [CITY_CENTER[1] + i * lon_step for i in range(-11, 11)]

lat_range, lon_range

([47.975100000000005,
  47.9911,
  48.0071,
  48.0231,
  48.039100000000005,
  48.0551,
  48.0711,
  48.0871,
  48.103100000000005,
  48.1191,
  48.1351,
  48.1511,
  48.1671,
  48.1831,
  48.1991,
  48.2151,
  48.2311,
  48.2471,
  48.2631,
  48.2791,
  48.2951],
 [11.318000000000001,
  11.342,
  11.366000000000001,
  11.39,
  11.414000000000001,
  11.438,
  11.462000000000002,
  11.486,
  11.510000000000002,
  11.534,
  11.558000000000002,
  11.582,
  11.606,
  11.63,
  11.654,
  11.678,
  11.702,
  11.726,
  11.75,
  11.774000000000001,
  11.798,
  11.822000000000001])

In [ ]:
# Collect the data through Google Place API
API_KEY = 'API_key'

CITY_CENTER = (48.1351, 11.5820)  # Munich center
RADIUS = 2000  # meters, safe to avoid overlap
lat_step = 0.016  # ~1.8 km
lon_step = 0.024  # ~1.8 km for Munich
QUERY = "supermarket"
TYPE  = 'supermarket'

# Create a grid of coordinates around the city center
lat_range = [CITY_CENTER[0] + i * lat_step for i in range(-10, 11)] # Effective total scan for 1st and 2nd run
lon_range = [CITY_CENTER[1] + i * lon_step for i in range(-11, 11)]

results = []

def fetch_places(lat, lon):
    url = (
        f"https://maps.googleapis.com/maps/api/place/textsearch/json"
        f"?query={QUERY}&location={lat},{lon}&radius={RADIUS}&type={TYPE}&key={API_KEY}"
    )
    data = requests.get(url).json()

    # The data looks like:
    # data = {
    #   'results': [place1, place2, ...],
    #   'next_page_token': 'abc...',
    #   'status': 'OK'}

    if 'results' in data:
        results.extend(data['results'])
    next_page_token = data.get('next_page_token')
    while next_page_token:
        time.sleep(2)  # Google requires a short delay before using next_page_token
        next_url = f"https://maps.googleapis.com/maps/api/place/textsearch/json?pagetoken={next_page_token}&key={API_KEY}"
        next_data = requests.get(next_url).json()
        results.extend(next_data.get('results', []))
        next_page_token = next_data.get('next_page_token')

# Run grid search
for lat in lat_range:
    for lon in lon_range:
        fetch_places(lat, lon)
        time.sleep(1)

# Deduplicate by place_id
unique_places = {place['place_id']: place for place in results}.values()

# Convert to DataFrame
df = pd.DataFrame([
    {
        'name': place['name'],
        'address': place.get('formatted_address'),
        'lat': place['geometry']['location']['lat'],
        'lon': place['geometry']['location']['lng'],
        'place_id': place['place_id'],
        'type': place.get('types', []),
        'rating': place.get('rating'),
        'user_ratings_total': place.get('user_ratings_total')
    }
    for place in unique_places
])

# Save to CSV
df.to_csv('grocery_stores_munich_raw.csv', index=False)
print(f"Collected {len(df)} unique grocery stores.")

Collected 1102 unique grocery stores.


In [14]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1102 entries, 0 to 1101
Data columns (total 8 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   name                1102 non-null   object 
 1   address             1102 non-null   object 
 2   lat                 1102 non-null   float64
 3   lon                 1102 non-null   float64
 4   place_id            1102 non-null   object 
 5   type                1102 non-null   object 
 6   rating              1085 non-null   float64
 7   user_ratings_total  1085 non-null   float64
dtypes: float64(4), object(4)
memory usage: 69.0+ KB


## Drop duplicates

In [15]:
print(len(df['place_id'].unique()))
duplicates = df[df.duplicated(['place_id'])]
duplicates
df.drop_duplicates(subset=['place_id'], inplace=True, ignore_index=True)
print(len(df['place_id'].unique()))
df

1102
1102


name                                            address  \
0           ALDI SÜD                 Emslanderstraße 3, 82319 Starnberg   
1       REWE express                        Perchastraße 10, 82335 Berg   
2              PENNY                  Weilheimer Str. 21, 82343 Pöcking   
3        EDEKA Azizi                  Weilheimer Str. 10, 82343 Pöcking   
4     Denns BioMarkt                Weilheimer Str. 14, 82319 Starnberg   
...              ...                                                ...   
1097  Franz Strixner               Großberghofener Str. 4, 85253 Erdweg   
1098     EDEKA Walla            Indersdorfer Str. 66, 85256 Vierkirchen   
1099           PENNY          Stumpfenbacher Str. 46, 85250 Altomünster   
1100            Lidl  Gewerbepark Altomünster, Stumpfenbacher Str. 4...   
1101         Nahkauf       Viktoria-von-Butler-Straße 2, 85244 Röhrmoos   

            lat        lon                     place_id  \
0     47.992430  11.331146  ChIJdbxavCzOnUcRTclr1b3d-Zo   
1     47.967685  11.357513  ChIJL0dcuCvPnUcRy3G70VnT8Cw   
2     47.964507  11.298337  ChIJTYQO_17OnUcREm-aWbeTSjg   
3     47.965690  11.298200  ChIJAeRUYF7OnUcRKH9YwQrxRo8   
4     47.991947  11.331027  ChIJCVzcur3PnUcR7Bz9OYPU6HE   
...         ...        ...                          ...   
1097  48.322924  11.292878  ChIJ2deVEwEOCUER7_OfPmQMclA   
1098  48.360691  11.443929  ChIJl-DsOW9knkcRW_BOLlxd5Eo   
1099  48.379754  11.259412  ChIJpwzcxhCJnkcReJH4v79U6Uk   
1100  48.380102  11.260002  ChIJP8re5BCJnkcRlsyn5lrVzok   
1101  48.328210  11.476792  ChIJmb8ROhllnkcRnnQOwTDNkDc   

                                                   type  rating  \
0     [supermarket, grocery_or_supermarket, store, f...     4.2   
1     [supermarket, grocery_or_supermarket, food, po...     NaN   
2     [supermarket, grocery_or_supermarket, food, po...     3.8   
3     [supermarket, grocery_or_supermarket, food, po...     3.3   
4     [convenience_store, supermarket, grocery_or_su...     4.2   
...                                                 ...     ...   
1097  [supermarket, grocery_or_supermarket, store, f...     4.9   
1098  [supermarket, grocery_or_supermarket, store, f...     4.1   
1099  [supermarket, grocery_or_supermarket, store, f...     3.9   
1100  [supermarket, grocery_or_supermarket, store, f...     4.5   
1101  [supermarket, shopping_mall, liquor_store, gro...     3.8   

      user_ratings_total  
0                  608.0  
1                    NaN  
2                  333.0  
3                  215.0  
4                   34.0  
...                  ...  
1097                39.0  
1098               225.0  
1099               167.0  
1100               319.0  
1101                12.0  

[1102 rows x 8 columns]

In [16]:
df.fillna(0, inplace=True) # some rating and total rating are nan

In [17]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1102 entries, 0 to 1101
Data columns (total 8 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   name                1102 non-null   object 
 1   address             1102 non-null   object 
 2   lat                 1102 non-null   float64
 3   lon                 1102 non-null   float64
 4   place_id            1102 non-null   object 
 5   type                1102 non-null   object 
 6   rating              1102 non-null   float64
 7   user_ratings_total  1102 non-null   float64
dtypes: float64(4), object(4)
memory usage: 69.0+ KB


In [18]:

"""
1. There are very few Rossmann-Drogeriemarkt: treated as Drug store; but why do we get so much DM stores?
2. Many "EDEKA+Place" stores: convert to 'Edeka'
3. Some special 'REWE Center' (2), 'REWE City' (2), 'REWE To Go' (1). 'REWE To Go bei Aral' (11)

"""
print(len(df['name'].unique()))
store_counts = df.groupby('name').size().reset_index(name='store_count').sort_values(by='store_count', ascending=False)
store_counts


329


name  store_count
258                                           REWE          125
212                                           Lidl           86
250                                          PENNY           76
65                                           EDEKA           69
14                                        ALDI SÜD           64
..                                             ...          ...
128                     EDEKA Türkyilmaz - München            1
125                                   EDEKA Turgut            1
124                       EDEKA Turan & Marienwald            1
123  EDEKA Theresie Inh. Kati Frank e.K. - München            1
328                                    فروشگاه ترک            1

[329 rows x 2 columns]

## Standardize the store names

In [19]:
# Normalize case and remove leading/trailing spaces
df['name'] = df['name'].str.strip().str.lower()

# Function to map based on keywords
def standardize_name(name):
    if 'edeka' in name:
        return 'Edeka'
    elif 'aldi' in name:
        return 'Aldi Süd'
    elif 'rewe' in name and not any(x in name for x in ['to go', 'center', 'city']):
        return 'Rewe'
    elif 'lidl' in name:
        return 'Lidl'
    elif 'kaufland' in name:
        return 'Kaufland'
    elif 'dm-drogerie' in name:
        return 'DM'
    elif 'hit supermarket' in name:
        return 'Hit'
    else:
        return name.title()  # fallback, capitalized

# Apply the function
df['name_standardized'] = df['name'].apply(standardize_name)

store_counts = df.groupby('name_standardized').size().reset_index(name='store_count').sort_values(by='store_count', ascending=False)
store_counts

name_standardized  store_count
62                                               Edeka          181
168                                               Rewe          147
14                                            Aldi Süd           91
119                                               Lidl           88
161                                              Penny           78
..                                                 ...          ...
82   Garagentore München Torbau Schwaben - Werksver...            1
83                               Gaßner 24/7 Smartshop            1
84                                         Gert Kirsch            1
85                                  Getränke Vis A Vis            1
216                                        فروشگاه ترک            1

[217 rows x 2 columns]

In [ ]:
df['name'] = df['name_standardized']
df.drop(columns=['name_standardized'], inplace=True)

## Filtering only the 'supermarket' type

In [5]:
import ast
df_filtered = df[df['type'].apply(
    lambda x: isinstance(x, str) and len(ast.literal_eval(x)) > 0 and ast.literal_eval(x)[0] == 'supermarket')]
df_filtered

name                                            address  \
0           Aldi Süd                 Emslanderstraße 3, 82319 Starnberg   
1               Rewe                        Perchastraße 10, 82335 Berg   
2              Penny                  Weilheimer Str. 21, 82343 Pöcking   
3              Edeka                  Weilheimer Str. 10, 82343 Pöcking   
5              Edeka                Weilheimer Str. 16, 82319 Starnberg   
...              ...                                                ...   
1097  Franz Strixner               Großberghofener Str. 4, 85253 Erdweg   
1098           Edeka            Indersdorfer Str. 66, 85256 Vierkirchen   
1099           Penny          Stumpfenbacher Str. 46, 85250 Altomünster   
1100            Lidl  Gewerbepark Altomünster, Stumpfenbacher Str. 4...   
1101         Nahkauf       Viktoria-von-Butler-Straße 2, 85244 Röhrmoos   

            lat        lon                     place_id  \
0     47.992430  11.331146  ChIJdbxavCzOnUcRTclr1b3d-Zo   
1     47.967685  11.357513  ChIJL0dcuCvPnUcRy3G70VnT8Cw   
2     47.964507  11.298337  ChIJTYQO_17OnUcREm-aWbeTSjg   
3     47.965690  11.298200  ChIJAeRUYF7OnUcRKH9YwQrxRo8   
5     47.991830  11.329611  ChIJEYGt6CzOnUcRSdy2CgcxZWY   
...         ...        ...                          ...   
1097  48.322924  11.292878  ChIJ2deVEwEOCUER7_OfPmQMclA   
1098  48.360691  11.443929  ChIJl-DsOW9knkcRW_BOLlxd5Eo   
1099  48.379754  11.259412  ChIJpwzcxhCJnkcReJH4v79U6Uk   
1100  48.380102  11.260002  ChIJP8re5BCJnkcRlsyn5lrVzok   
1101  48.328210  11.476792  ChIJmb8ROhllnkcRnnQOwTDNkDc   

                                                   type  rating  \
0     ['supermarket', 'grocery_or_supermarket', 'sto...     4.2   
1     ['supermarket', 'grocery_or_supermarket', 'foo...     0.0   
2     ['supermarket', 'grocery_or_supermarket', 'foo...     3.8   
3     ['supermarket', 'grocery_or_supermarket', 'foo...     3.3   
5     ['supermarket', 'grocery_or_supermarket', 'sto...     3.9   
...                                                 ...     ...   
1097  ['supermarket', 'grocery_or_supermarket', 'sto...     4.9   
1098  ['supermarket', 'grocery_or_supermarket', 'sto...     4.1   
1099  ['supermarket', 'grocery_or_supermarket', 'sto...     3.9   
1100  ['supermarket', 'grocery_or_supermarket', 'sto...     4.5   
1101  ['supermarket', 'shopping_mall', 'liquor_store...     3.8   

      user_ratings_total name_standardized  
0                  608.0          Aldi Süd  
1                    0.0              Rewe  
2                  333.0             Penny  
3                  215.0             Edeka  
5                  460.0             Edeka  
...                  ...               ...  
1097                39.0    Franz Strixner  
1098               225.0             Edeka  
1099               167.0             Penny  
1100               319.0              Lidl  
1101                12.0           Nahkauf  

[995 rows x 9 columns]

In [ ]:
store_counts = df_filtered.groupby('name').size().reset_index(name='store_count').sort_values(by='store_count', ascending=False)
store_counts

name_standardized  store_count
53                                               Edeka          179
147                                               Rewe          147
14                                            Aldi Süd           91
104                                               Lidl           88
141                                              Penny           78
..                                                 ...          ...
69                             Frisch Markt Haimhausen            1
70                                   Frischemarkt Koch            1
72                                  Galeria Markthalle            1
73   Garagentore München Torbau Schwaben - Werksver...            1
187                                        فروشگاه ترک            1

[188 rows x 2 columns]

In [8]:
top50 = store_counts.sort_values(by=['store_count'], ascending=False).iloc[0:50].reset_index()#.drop(4) # removing DM, need 'reset_index()' before 'drop()'
top50

index                       name_standardized  store_count
0      53                                   Edeka          179
1     147                                    Rewe          147
2      14                                Aldi Süd           91
3     104                                    Lidl           88
4     141                                   Penny           78
5     130                   Netto Marken-Discount           42
6     133                           Norma Filiale           33
7     151                     Rewe To Go Bei Aral           22
8      51                                E Xpress           21
9     129                              Netto City           18
10     97                                Kaufland           14
11     17              Alnatura Super Natur Markt           13
12    180                     Vollcorner Biomarkt           10
13    169              Tegut... Gute Lebensmittel            9
14     84                          Hit Supermarkt            9
15     71                    Fristo Getränkemarkt            9
16    160                            Spar Express            8
17     59                                Euroshop            8
18    127                                 Nahkauf            5
19     44                                E Center            5
20    149                               Rewe City            4
21    148                             Rewe Center            4
22    150                              Rewe To Go            4
23     33            Bonus-Markt Ihr Nahversorger            3
24    168                                   Tegut            3
25    155                        Sahan Supermarkt            2
26    132                                   Norma            2
27     35                        Burak Supermarkt            2
28    181                   Weihnachtsbaumverkauf            2
29    171                          Tia Y Tio 24/7            2
30      6               Aez Dachau Getränkecenter            1
31     15                           Alfafood Gmbh            1
32      8                    Aez Germering Im Gep            1
33      9              Aez Ikarus Center Puchheim            1
34     11                             Aez Isartal            1
35     22                           Asia Feinkost            1
36     12                         Aez Martinsried            1
37     13                            Aez Puchheim            1
38     19   Alönuschka Russian Specialties Munich            1
39     16                                 Allguth            1
40     18  Alsham Supermarkt محمصة و مكسرات الشام            1
41     20                         Apna Desi Store            1
42     21         Arcade Organic Market (Tagwerk)            1
43     48                          E Center Seker            1
44     49                          E Center Sempt            1
45     50                       E Center Sostaric            1
46     87             Ideal Türkischer Supermarkt            1
47      7     Aez Germering Getränkecenter Im Gep            1
48     41                    Delta-Markt Neumaier            1
49      5                              Aez Dachau            1

In [9]:
store_df = df_filtered[df_filtered['name_standardized'].isin(top50['name_standardized'])]
store_df

name  \
0                  Aldi Süd   
1                      Rewe   
2                     Penny   
3                     Edeka   
5                     Edeka   
...                     ...   
1094  Netto Marken-Discount   
1098                  Edeka   
1099                  Penny   
1100                   Lidl   
1101                Nahkauf   

                                                address        lat        lon  \
0                    Emslanderstraße 3, 82319 Starnberg  47.992430  11.331146   
1                           Perchastraße 10, 82335 Berg  47.967685  11.357513   
2                     Weilheimer Str. 21, 82343 Pöcking  47.964507  11.298337   
3                     Weilheimer Str. 10, 82343 Pöcking  47.965690  11.298200   
5                   Weilheimer Str. 16, 82319 Starnberg  47.991830  11.329611   
...                                                 ...        ...        ...   
1094                  Erdinger Str. 143, 85356 Freising  48.384031  11.765215   
1098            Indersdorfer Str. 66, 85256 Vierkirchen  48.360691  11.443929   
1099          Stumpfenbacher Str. 46, 85250 Altomünster  48.379754  11.259412   
1100  Gewerbepark Altomünster, Stumpfenbacher Str. 4...  48.380102  11.260002   
1101       Viktoria-von-Butler-Straße 2, 85244 Röhrmoos  48.328210  11.476792   

                         place_id  \
0     ChIJdbxavCzOnUcRTclr1b3d-Zo   
1     ChIJL0dcuCvPnUcRy3G70VnT8Cw   
2     ChIJTYQO_17OnUcREm-aWbeTSjg   
3     ChIJAeRUYF7OnUcRKH9YwQrxRo8   
5     ChIJEYGt6CzOnUcRSdy2CgcxZWY   
...                           ...   
1094  ChIJNRcM7BfJnkcRjOGlvFhU-vg   
1098  ChIJl-DsOW9knkcRW_BOLlxd5Eo   
1099  ChIJpwzcxhCJnkcReJH4v79U6Uk   
1100  ChIJP8re5BCJnkcRlsyn5lrVzok   
1101  ChIJmb8ROhllnkcRnnQOwTDNkDc   

                                                   type  rating  \
0     ['supermarket', 'grocery_or_supermarket', 'sto...     4.2   
1     ['supermarket', 'grocery_or_supermarket', 'foo...     0.0   
2     ['supermarket', 'grocery_or_supermarket', 'foo...     3.8   
3     ['supermarket', 'grocery_or_supermarket', 'foo...     3.3   
5     ['supermarket', 'grocery_or_supermarket', 'sto...     3.9   
...                                                 ...     ...   
1094  ['supermarket', 'grocery_or_supermarket', 'sto...     3.8   
1098  ['supermarket', 'grocery_or_supermarket', 'sto...     4.1   
1099  ['supermarket', 'grocery_or_supermarket', 'sto...     3.9   
1100  ['supermarket', 'grocery_or_supermarket', 'sto...     4.5   
1101  ['supermarket', 'shopping_mall', 'liquor_store...     3.8   

      user_ratings_total      name_standardized  
0                  608.0               Aldi Süd  
1                    0.0                   Rewe  
2                  333.0                  Penny  
3                  215.0                  Edeka  
5                  460.0                  Edeka  
...                  ...                    ...  
1094               392.0  Netto Marken-Discount  
1098               225.0                  Edeka  
1099               167.0                  Penny  
1100               319.0                   Lidl  
1101                12.0                Nahkauf  

[857 rows x 9 columns]

In [ ]:
store_df.to_csv('supermarket_Munich_cleaned_filtered_top50.csv')

In [148]:
fig = px.scatter_map(df, lat="lat", lon="lon", color="name_standardized", size="rating",
                  color_continuous_scale=px.colors.cyclical.IceFire, size_max=3, zoom=6,
                  map_style="carto-positron",
                  color_discrete_sequence=px.colors.qualitative.Set2,  # Or 'Plotly', 'Dark2', etc.
                  hover_name="name",  # Label shown in bold
                  hover_data={
                        "name_standardized": True,
                        "address": True,
                        "type": True,
                        "rating": True,
                        "lat": True,
                        "lon": True
                    },
                #animation_frame="commissioning_year"

                  )

fig.update_traces(
    hovertemplate="<b>%{customdata[0]}</b><br>Address: %{customdata[1]}<br>Type: %{customdata[2]}<br>Rate: %{customdata[3]}<br>Lat: %{customdata[4]}<br>Lon: %{customdata[5]}<br><extra></extra>"
)
fig.update_layout(
    width=1200,  # in pixels
    height=800)
fig.show()

# Population data on a grid of 100m step size

## Key Data Collection and Preprocessing Results
- Successfully collected and deduplicated supermarket locations in Munich using the Google Places API, resulting in a high-quality dataset of the top 50 supermarket brands.
- Integrated and geocoded high-resolution population data on a 100m grid, filtered for the Munich area.
- Standardized store names and filtered for relevant types to ensure accurate downstream analysis.
- Visualized both supermarket and population distributions, providing a strong foundation for spatial opportunity modeling.

In [ ]:
chunk_size = 100_000  # Try 100k or 1M rows per chunk to load the large data file
chunks = pd.read_csv(
    '/Bevoelkerung100M.csv',
    sep=';',
    encoding="latin1",
    chunksize=chunk_size,
    usecols=['Gitter_ID_100m', 'Merkmal', 'Auspraegung_Text', 'Anzahl']  # only needed columns
)

In [ ]:
# Coordinate transformation
transformer = Transformer.from_crs("epsg:3035", "epsg:4326", always_xy=True)

def extract_coords(gid):
    match = re.match(r'100mN(\d+)E(\d+)', gid)
    if match:
        north = int(match.group(1)) * 100
        east = int(match.group(2)) * 100
        return east, north
    else:
        return None, None

result_list = []

for chunk in chunks:
    # Filter relevant rows only
    filtered = chunk[
        (chunk['Merkmal'].str.strip() == 'INSGESAMT') &
        (chunk['Auspraegung_Text'].str.strip() == 'Einheiten insgesamt')
    ].copy()

    # Extract coords
    filtered[['easting', 'northing']] = filtered['Gitter_ID_100m'].apply(
        lambda x: pd.Series(extract_coords(x))
    )

    # Convert to lat/lon
    filtered[['lon', 'lat']] = filtered.apply(
        lambda row: pd.Series(transformer.transform(row['easting'], row['northing'])),
        axis=1
    )

    # Filter for Munich bounding box
    filtered = filtered[
        (filtered['lat'] > 48.00) & (filtered['lat'] < 48.30) &
        (filtered['lon'] > 11.30) & (filtered['lon'] < 11.80)
    ]
# lan and lon range for collecting Store info
# 48.00-48.35
# 11.31-11.85

    # Keep relevant columns
    result_list.append(filtered[['lat', 'lon', 'Anzahl', 'easting', 'northing']])

In [41]:
df_result = pd.concat(result_list)
df_result.rename(columns={'Anzahl': 'population'}, inplace=True)

In [42]:
df_result.to_csv('munich_population_points.csv', index=False)

In [115]:
pop_df = pd.read_csv('munich_population_points.csv')

In [116]:
fig = px.scatter_map(pop_df, lat="lat", lon="lon", color="population", size="population",
                  color_continuous_scale=px.colors.cyclical.IceFire, size_max=6, zoom=6,
                  map_style="carto-positron",
                  color_discrete_sequence=px.colors.qualitative.Set2,  # Or 'Plotly', 'Dark2', etc.
                  range_color=[0, 400],
                  hover_name="population",  # Label shown in bold
                  hover_data={
                        "lat": True,
                        "lon": True,
                        "population": True
                    },
                  )

fig.update_traces(
    hovertemplate="<b>lat: %{customdata[0]}</b><br>lon: %{customdata[1]}<br>population: %{customdata[2]}<br><extra></extra>"
)
fig.show()